In [3]:
import pandas as pd
import numpy as np
import tokenization

import tensorflow as tf
import tensorflow_hub as hub
import tensorflow_addons as tfa

import sklearn
from sklearn.model_selection import train_test_split

c:\Users\macty\AppData\Local\Programs\Python\Python311\Lib\site-packages\tensorflow_addons\utils\tfa_eol_msg.py:23: UserWarning: 

TensorFlow Addons (TFA) has ended development and introduction of new features.
TFA has entered a minimal maintenance and release mode until a planned end of life in May 2024.
Please modify downstream libraries to take dependencies from other repositories in our TensorFlow community (e.g. Keras, Keras-CV, and Keras-NLP). 

For more information see: https://github.com/tensorflow/addons/issues/2807 

  warnings.warn(


In [4]:
acts=pd.read_csv('data-only_dialogue_acts/user_acts.csv',index_col=None)

In [5]:
acts.head()

Agent                                               text      Act  ack  \
0  user             W jakim kraju mogę zarezerwować hotel?     help  NaN   
1  user  Przedstaw proszę oferty z obszaru Górnego Kara...  request  NaN   
2  user                                                  3   inform  NaN   
3  user                                  1000 USD na osobę   inform  NaN   
4  user                 Ostatni tydzień maja 2023 na 6 dni   inform  NaN   

   affirm  bye  hello  help  negate  null  repeat  reqalts  reqmore  restart  \
0     NaN  NaN    NaN   NaN     NaN   NaN     NaN      NaN      NaN      NaN   
1     NaN  NaN    NaN   NaN     NaN   NaN     NaN      NaN      NaN      NaN   
2     NaN  NaN    NaN   NaN     NaN   NaN     NaN      NaN      NaN      NaN   
3     NaN  NaN    NaN   NaN     NaN   NaN     NaN      NaN      NaN      NaN   
4     NaN  NaN    NaN   NaN     NaN   NaN     NaN      NaN      NaN      NaN   

   silence  thankyou  confirm  deny  inform  request  
0      NaN       NaN      NaN   NaN     NaN      NaN  
1      NaN       NaN      NaN   NaN     NaN      NaN  
2      NaN       NaN      NaN   NaN     NaN      NaN  
3      NaN       NaN      NaN   NaN     NaN      NaN  
4      NaN       NaN      NaN   NaN     NaN      NaN

In [6]:
for column in acts.columns[3:]:
    acts[column]=acts["Act"].str.contains(column).astype(int)

In [7]:
acts.to_csv('user_acts_one_hot.csv')

In [8]:
acts=acts.drop(["Agent"],axis=1)
acts=acts.drop(["Act"],axis=1)

In [9]:
text = acts["text"]
labels = acts.drop(["text"],axis=1)

In [10]:
label_cols=labels.columns
labels=labels[labels.columns].values

In [11]:
text = np.array(text)

In [12]:
text

array(['W jakim kraju mogę zarezerwować hotel?',
       'Przedstaw proszę oferty z obszaru Górnego Karabachu', '3',
       '1000 USD na osobę', 'Ostatni tydzień maja 2023 na 6 dni',
       'Gorąca woda i bezpieczna okolica',
       'Podaj proszę kosztorys dla hotelu YY',
       'Czy jest to cena łączna dla 3 osób?',
       'Czy oferta zawiera ubezpieczenie?',
       'Ile wynosi łączna cena z ubezpieczeniem dla 3 osób?',
       'Rezygnuję z rezerwacji. Potrzebuję więcej czasu do namysłu.',
       'chciałbym zwiedzić coś egzotycznego. Co możesz mi zaproponować?',
       'tam jest trochę za zimno',
       'brzmi bardzo fajnie! Jakie są ceny hoteli w Brazylii?',
       'Chciałbym aby to był pokój dla 2 osób i doga',
       'Dzień dobry. Chciałbym wybrać się do warszawy na przyszły weekend. Szukam pokoi dla dwóch osób w cenie do 500 zł za noc.',
       'Zależałoby mi na śniadaniu oraz na tym żeby hotel był blisko centrum miasta. Miło by było jakby był dostępny basen.',
       'Poproszę w ta

In [13]:
from transformers import *
tokenizer = BertTokenizer.from_pretrained("dkleczek/bert-base-polish-uncased-v1")
model = TFBertForSequenceClassification.from_pretrained("dkleczek/bert-base-polish-uncased-v1", from_pt=True, num_labels=17)



c:\Users\macty\AppData\Local\Programs\Python\Python311\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
c:\Users\macty\AppData\Local\Programs\Python\Python311\Lib\site-packages\transformers\generation_utils.py:24: FutureWarning: Importing `GenerationMixin` from `src/transformers/generation_utils.py` is deprecated and will be removed in Transformers v5. Import as `from transformers import GenerationMixin` instead.
  warnings.warn(
c:\Users\macty\AppData\Local\Programs\Python\Python311\Lib\site-packages\transformers\generation_tf_utils.py:24: FutureWarning: Importing `TFGenerationMixin` from `src/transformers/generation_tf_utils.py` is deprecated and will be removed in Transformers v5. Import as `from transformers import TFGenerationMixin` instead.
  warnings.warn(
loading file vocab.txt from cache at C:\Users\macty/

In [14]:
acts_text= [tokenizer.encode(text, add_special_tokens=True, max_length=128, padding='max_length', truncation=True) for text in acts["text"]]

In [15]:
input_ids = np.array(acts_text)
attention_masks = np.where(input_ids != 0, 1, 0) # checks for existing words

In [16]:
train_inputs, test_inputs, train_labels, test_labels = train_test_split(input_ids, labels, test_size=0.2, random_state=42)
train_masks, test_masks, _, _ = train_test_split(attention_masks, input_ids, test_size=0.2, random_state=42)

In [17]:
optimizer = tf.keras.optimizers.Adam(learning_rate=2e-5)
loss = tf.keras.losses.BinaryCrossentropy(from_logits=True)
metrics = tfa.metrics.F1Score(num_classes=17, threshold=0.5)
model.layers[-1].activation = tf.keras.activations.sigmoid
model.compile(optimizer=optimizer, loss=loss, metrics=metrics)

In [34]:
history = model.fit(
    [train_inputs, train_masks],
    train_labels,
    validation_data=([test_inputs, test_masks], test_labels),
    batch_size=32,
    epochs=30
)

Epoch 1/30
4/4 [==============================] - 63s 15s/step - loss: 0.1764 - f1_score: 0.1641 - val_loss: 0.1709 - val_f1_score: 0.1149
Epoch 2/30
4/4 [==============================] - 59s 15s/step - loss: 0.1712 - f1_score: 0.1957 - val_loss: 0.1672 - val_f1_score: 0.1280
Epoch 3/30
4/4 [==============================] - 59s 15s/step - loss: 0.1636 - f1_score: 0.1932 - val_loss: 0.1633 - val_f1_score: 0.1385
Epoch 4/30
4/4 [==============================] - 59s 15s/step - loss: 0.1574 - f1_score: 0.2331 - val_loss: 0.1592 - val_f1_score: 0.1627
Epoch 5/30
4/4 [==============================] - 59s 15s/step - loss: 0.1519 - f1_score: 0.2435 - val_loss: 0.1554 - val_f1_score: 0.1627
Epoch 6/30
4/4 [==============================] - 60s 15s/step - loss: 0.1471 - f1_score: 0.2603 - val_loss: 0.1516 - val_f1_score: 0.1646
Epoch 7/30
4/4 [==============================] - 59s 15s/step - loss: 0.1417 - f1_score: 0.2654 - val_loss: 0.1494 - val_f1_score: 0.1627
Epoch 8/30
4/4 [===========

In [38]:
input_sentence = "do widzenia"
inputs = tokenizer.encode_plus(input_sentence, add_special_tokens=True, return_tensors='tf')
predictions = model.predict([inputs['input_ids'], inputs['attention_mask']])
print(predictions)

1/1 [==============================] - 0s 64ms/step
TFSequenceClassifierOutput(loss=None, logits=array([[0.06025698, 0.04095593, 0.7684139 , 0.04259768, 0.05270579,
        0.10895084, 0.03345573, 0.03596378, 0.0508336 , 0.05108728,
        0.04185295, 0.06173437, 0.21573795, 0.10289352, 0.05192397,
        0.07420129, 0.08625325]], dtype=float32), hidden_states=None, attentions=None)


In [40]:
model.save('model', save_format='tf')

INFO:tensorflow:Assets written to: model\assets


INFO:tensorflow:Assets written to: model\assets
